<a href="https://colab.research.google.com/github/ajithprinc/face_editing_using_GAN_with_edits/blob/connected_with_my_drive/Copy_of_2_Face_Editing_Notebook.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Notebook II: Playing with Latent Codes

![alt text](https://raw.githubusercontent.com/tr1pzz/InterFaceGAN/master/teaser.jpg)

# OK, first, the really annoying part:
### Google Colab uses TensorFlow version 1.14 by default (which comes with Cuda 10.0)
### Unfortunately the repo we'll be using requires TF version 1.12 and Cuda 9.0...

In [1]:
%tensorflow_version 1.x

import tensorflow as tf

print(tf.__version__)

TensorFlow 1.x selected.
1.15.2


In [3]:
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2020 NVIDIA Corporation
Built on Wed_Jul_22_19:09:09_PDT_2020
Cuda compilation tools, release 11.0, V11.0.221
Build cuda_11.0_bu.TC445_37.28845127_0


## Annoying part 1 of 2: Downgrade to TensorFlow 1.12.2

In [4]:
#!pip install --upgrade tensorflow-gpu==1.12.2

ERROR: Could not find a version that satisfies the requirement tensorflow-gpu==1.12.2 (from versions: 1.13.1, 1.13.2, 1.14.0, 1.15.0rc0, 1.15.0rc1, 1.15.0rc2, 1.15.0rc3, 1.15.0, 1.15.2, 1.15.3, 1.15.4, 1.15.5, 2.0.0a0, 2.0.0b0, 2.0.0b1, 2.0.0rc0, 2.0.0rc1, 2.0.0rc2, 2.0.0, 2.0.1, 2.0.2, 2.0.3, 2.0.4, 2.1.0rc0, 2.1.0rc1, 2.1.0rc2, 2.1.0, 2.1.1, 2.1.2, 2.1.3, 2.2.0rc0, 2.2.0rc1, 2.2.0rc2, 2.2.0rc3, 2.2.0rc4, 2.2.0, 2.2.1, 2.2.2, 2.3.0rc0, 2.3.0rc1, 2.3.0rc2, 2.3.0, 2.3.1, 2.3.2, 2.4.0rc0, 2.4.0rc1, 2.4.0rc2, 2.4.0rc3, 2.4.0rc4, 2.4.0, 2.4.1, 2.5.0rc0, 2.5.0rc1)
ERROR: No matching distribution found for tensorflow-gpu==1.12.2


## Annoying part 2 of 2: Install Cuda 9.0 (this can take a few minutes, be patient)

In [1]:
!wget https://developer.nvidia.com/compute/cuda/9.0/Prod/local_installers/cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64-deb
!dpkg -i cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64-deb
!apt-key add /var/cuda-repo-9-0-local/7fa2af80.pub
!apt-get update
!apt-get install cuda=9.0.176-1
!echo ****** Cuda reinstall completed. Restart runtime now! *******

--2021-04-14 03:07:56--  https://developer.nvidia.com/compute/cuda/9.0/Prod/local_installers/cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64-deb
Resolving developer.nvidia.com (developer.nvidia.com)... 152.199.16.29
Connecting to developer.nvidia.com (developer.nvidia.com)|152.199.16.29|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://developer.nvidia.com/compute/cuda/9.0/prod/local_installers/cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64-deb [following]
--2021-04-14 03:07:57--  https://developer.nvidia.com/compute/cuda/9.0/prod/local_installers/cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64-deb
Reusing existing connection to developer.nvidia.com:443.
HTTP request sent, awaiting response... 302 Found
Location: https://developer.download.nvidia.com/compute/cuda/9.0/secure/Prod/local_installers/cuda-repo-ubuntu1604-9-0-local_9.0.176-1_amd64.deb?5UXD2Bdjjzlc6iW_r5UEfUr69ygDyqxld7_OHduTrDW5Rz-pOKyMiDAUfz4KBfK5efkvrkZj5elmZxBJ99myQRDarMd4Whu

## When the above cell has finished executing, restart the kernel runtime to reload everything
> * At the top, click 'Runtime --> restart runtime'
> * Continue with the cells below!
> * In fact, let's just pretend that annoying part never happened...

### Safety check to see if everything worked:
(This might not work as intended due to TF 1.12 being a very old / deprecated version of TensorFlow...) 

In [1]:
%tensorflow_version 1.x
import tensorflow as tf

#print("Now running TensorFlow version %s on Colab!" %tf.VERSION)
#assert tf.VERSION == '1.12.2'

TensorFlow 1.x selected.


In [2]:
!nvcc --version 

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2017 NVIDIA Corporation
Built on Fri_Sep__1_21:08:03_CDT_2017
Cuda compilation tools, release 9.0, V9.0.176


## If the above cells showed TensorFlow version 1.12.2 and Cuda release 9.0, you're good to go!
![alt text](https://media.giphy.com/media/CjmvTCZf2U3p09Cn0h/giphy.gif)

## Clone my fork of InterFaceGAN
### Original Repo: https://github.com/ShenYujun/InterFaceGAN

### Paper: https://arxiv.org/abs/1907.10786

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [19]:
cd /content/drive/MyDrive/InterFaceGAN

/content/drive/MyDrive/InterFaceGAN


In [3]:
#!cp -r /content/InterFaceGAN /content/drive/MyDrive
#!git clone https://github.com/tr1pzz/InterFaceGAN.git

Cloning into 'InterFaceGAN'...
remote: Enumerating objects: 127, done.
remote: Total 127 (delta 0), reused 0 (delta 0), pack-reused 127
Receiving objects: 100% (127/127), 2.06 MiB | 1.98 MiB/s, done.
Resolving deltas: 100% (14/14), done.


## Download the pretrained StyleGAN FFHQ network from NVIDIA:

In [6]:
#moving pretrained StyleGAN FFHQ
#import shutil
#shutil.copy2('/content/drive/MyDrive/pickle_files/karras2019stylegan-ffhq-1024x1024_1.pkl', '/content/InterFaceGAN/models/pretrain')

'/content/InterFaceGAN/models/pretrain/karras2019stylegan-ffhq-1024x1024_1.pkl'

In [ ]:
#!gdown https://drive.google.com/uc?id=1MEGjdvVpUsu1jB4zrXZN7Y4kBBOzizDQ
#!mv /content/InterFaceGAN/karras2019stylegan-ffhq-1024x1024.pkl /content/IanterFaceGAN/models/pretrain/karras2019stylegan-ffhq-1024x1024.pkl

Permission denied: https://drive.google.com/uc?id=1MEGjdvVpUsu1jB4zrXZN7Y4kBBOzizDQ
Maybe you need to change permission over 'Anyone with the link'?
mv: cannot stat '/content/InterFaceGAN/karras2019stylegan-ffhq-1024x1024.pkl': No such file or directory


# I. Let's load our latent space vectors:
Manually upload the output_vectors.npy file (the one you downloaded at the end of notebook I) to the root of the directory
*   Right-click anywhere inside the Files browser --> "Upload"
*   Make sure the filename is "output_vectors.npy"



In [20]:
shutil.copy2('/content/drive/MyDrive/face_npy/output_vectors.npy','/content/')
import numpy as np
final_w_vectors = np.load('/content/output_vectors.npy')

print("%d latent vectors of shape %s loaded from %s!" %(final_w_vectors.shape[0], str(final_w_vectors.shape[1:]), 'output_vectors.npy'))

2 latent vectors of shape (18, 512) loaded from output_vectors.npy!


## The InterFaceGAN comes with a bunch of pretrained latent directions
### (However, you can also train your own!!)
### Pick the latent space manipulation we want to use (added it as the -b argument below)

Boundaries: https://github.com/ShenYujun/InterFaceGAN/tree/master/boundaries
* stylegan_ffhq_age_w_boundary.npy
* stylegan_ffhq_eyeglasses_w_boundary.npy
* stylegan_ffhq_gender_w_boundary.npy
* stylegan_ffhq_pose_w_boundary.npy
* stylegan_ffhq_smile_w_boundary.npy


# II. Let's configure our latent-space interpolation
### Change the settings below to morph the faces:

In [4]:
latent_direction = 'eyeglasses'     #### Pick one of ['age', 'eyeglasses', 'gender', 'pose', 'smile']
morph_strength = 3           # Controls how strongly we push the face into a certain latent direction (try 1-5)
nr_interpolation_steps = 48  # The amount of intermediate steps/frames to render along the interpolation path

# III. Run the latent space manipulation & generate images:

In [5]:
boundary_file = 'stylegan_ffhq_%s_w_boundary.npy' %latent_direction

print("Ready to start manipulating faces in the ** %s ** direction!" %latent_direction)
print("Interpolation from %d to %d with %d intermediate frames." %(-morph_strength, morph_strength, nr_interpolation_steps))
print("\nLoading latent directions from %s" %boundary_file)

Ready to start manipulating faces in the ** eyeglasses ** direction!
Interpolation from -3 to 3 with 48 intermediate frames.

Loading latent directions from stylegan_ffhq_eyeglasses_w_boundary.npy



## Final note: The code cell below has a bug I still need to fix...
### First time you run it, it will give an error.


## Ready? Set, Go!

In [27]:
import subprocess
return_code = subprocess.call("rm -r results/%s" %latent_direction, shell=True)

run_command = "python edit.py \
      -m stylegan_ffhq \
      -b boundaries/stylegan_ffhq_%s_w_boundary.npy \
      -s Wp \
      -i '/content/output_vectors.npy' \
      -o results/%s \
      --start_distance %.2f \
      --end_distance %.2f \
      --steps=%d" %(latent_direction, latent_direction, -morph_strength, morph_strength, nr_interpolation_steps)


print("Running latent interpolations... This should not take longer than ~1 minute")
print("Running: %s" %run_command)
return_code = subprocess.call(run_command, shell=True)

if not return_code:
  print("Latent interpolation successfully dumped to disk!")
else:
  print("Something went wrong, try re-executing this cell...")

Running latent interpolations... This should not take longer than ~1 minute
Running: python edit.py       -m stylegan_ffhq       -b boundaries/stylegan_ffhq_eyeglass_w_boundary.npy       -s Wp       -i '/content/output_vectors.npy'       -o results/eyeglass       --start_distance -3.00       --end_distance 3.00       --steps=48
Something went wrong, try re-executing this cell...
Running latent interpolations... This should not take longer than ~1 minute
Running: python edit.py       -m stylegan_ffhq       -b boundaries/stylegan_ffhq_eyeglass_w_boundary.npy       -s Wp       -i '/content/output_vectors.npy'       -o results/eyeglass       --start_distance -3.00       --end_distance 3.00       --steps=48


### If you're still getting errors, run the command with output to see what's wrong: (Adjust the arguments below as needed)
### Otherwise ---> just skip this cell

In [ ]:
'models/pretrain/karras2019stylegan-ffhq-1024x1024.pkl'
'models/pretrain/karras2019stylegan-ffhq-1024x1024.pkl.pth'

In [7]:
'''if 1:
  latent_direction = 'eyeglasses'
  !rm -r results/
  !python edit.py \
    -m stylegan_ffhq \
    -b boundaries/stylegan_ffhq_eyeglasses_w_boundary.npy \
    -s Wp \
    -i '/content/output_vectors.npy' \
    -o results/eyeglass \
    --start_distance -3.0 \
    --end_distance 3.0 \
    --steps=48'''

[2021-04-14 03:31:33,794][INFO] Initializing generator.
models/pretrain/stylegan_ffhq.pth
models/pretrain/karras2019stylegan-ffhq-1024x1024.pkl
[2021-04-14 03:31:34,081][INFO] Loading pytorch model from `models/pretrain/stylegan_ffhq.pth`.
[2021-04-14 03:31:34,393][INFO] Successfully loaded!
[2021-04-14 03:31:36,468][INFO] Preparing boundary.
[2021-04-14 03:31:36,476][INFO] Preparing latent codes.
[2021-04-14 03:31:36,477][INFO]   Load latent codes from `/content/output_vectors.npy`.
[2021-04-14 03:31:36,478][INFO] Editing 2 samples.
[2021-04-14 03:31:51,940][INFO] Successfully edited 2 samples.


# IV. Finally, turn the results into pretty movies!
Adjust which video to render & at what framerate:

In [22]:
image_folder = '/content/drive/MyDrive/InterFaceGAN/results/%s' %latent_direction
video_fps = 12.

### Render the videos:

In [23]:
from moviepy.editor import *
import cv2

out_path = '/content/output_videos/'

images = [img_path for img_path in sorted(os.listdir(image_folder)) if '.jpg' in img_path]
os.makedirs(out_path, exist_ok=True)

prev_id = None
img_sets = []
for img_path in images:
  img_id = img_path.split('_')[0]
  if img_id == prev_id: #append
    img_sets[-1].append(img_path)
    
  else: #start a new img set
    img_sets.append([])
    img_sets[-1].append(img_path)
  prev_id = img_id

print("Found %d image sets!\n" %len(img_sets))
if image_folder[-1] != '/':
  image_folder += '/'

def make_video(images, vid_name):
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    video = cv2.VideoWriter(vid_name, fourcc, video_fps, (1024, 1024))
    gen = {}
    for img in images:
      video.write(img)
    video.release()
    print('finished '+ vid_name)
    
    
for i in range(len(img_sets)):
  print("############################")
  print("\nGenerating video %d..." %i)
  set_images = []
  vid_name = out_path + 'out_video_%s_%02d.mp4' %(latent_direction,i)
  for img_path in img_sets[i]:
    set_images.append(cv2.imread(image_folder + img_path))

  set_images.extend(reversed(set_images))
  make_video(set_images, vid_name)

Found 0 image sets!



# So... What did we get?
![alt text](https://encrypted-tbn0.gstatic.com/images?q=tbn:ANd9GcTiWSY0xWfAJvKOBUhvVFcewroGDzAe1lNMfi73EAJp4IBJ-6zi)

## Option 1: 
> ### Navigate to output_videos/
> (you might have to "REFRESH" the Filebrowser)
> ### Download the videos to your local pc
> (This makes viewing a bit easier + you can share them :p)

## Option 2:
> ### Display the videos right here in the notebook

## Visualise the resulting videos inside this Notebook:

In [10]:
video_file_to_show = 0

clip = VideoFileClip('/content/output_videos/out_video_%s_%02d.mp4' %(latent_direction, video_file_to_show))
clip.ipython_display(height=512, autoplay=1, loop=1)

 99%|█████████▉| 96/97 [00:01<00:00, 50.28it/s]


In [11]:
video_file_to_show = 1

clip = VideoFileClip('/content/output_videos/out_video_%s_%02d.mp4' %(latent_direction, video_file_to_show))
clip.ipython_display(height=512, autoplay=1, loop=1)


 99%|█████████▉| 96/97 [00:01<00:00, 50.20it/s]


# V. Your turn to experiment

## You now have all the tools to start exploring the latent Space of StyleGAN: HAVE FUN!
### StyleGAN paper link: https://arxiv.org/abs/1812.04948

### Some things you could try:
* You can blend between two faces by doing a linear interpolation in the latent space: very cool!
*   The StyleGAN vector has 18x512 dimensions, each of those 18 going into a different layer of the generator...
*   You could eg take the first 9 from person A and the next 9 from person B
*   This is why it's called "Style-GAN": you can manipulate the style of an image at multiple levels of the Generator!
*   Try interpolating in Z-space rather than in W-space (see InterFaceGan paper & repo)
* Have Fun!!
# Find something cool you wanna share? 
## ---> Tag me on Twitter @xsteenbrugge: https://twitter.com/xsteenbrugge
## ---> Or simply share it in the comments on YouTube!

![alt text](https://media.makeameme.org/created/experiment.jpg)